<a href="https://colab.research.google.com/github/tarunprabhu45/Quantum-Text-Encoding/blob/main/quantum.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [3]:
!pip install qiskit qiskit-ibm-runtime datasets transformers scikit-learn matplotlib numpy nltk --quiet


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 149.4/149.4 kB 4.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.8/6.8 MB 75.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.0/3.0 MB 83.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 42.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 13.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 20.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 340.8/340.8 kB 34.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 16.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 434.9/434.9 kB 38.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 93.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 95.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.5/49.5 kB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49

In [2]:
import logging # import the logging module
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt



In [5]:
from datasets import load_dataset
def load_common_corpus_metadata(sample_size=100):
    """
    Load metadata or a small subset of the Common Corpus dataset.
    :param sample_size: Number of samples to load for demonstration/testing purposes.
    :return: Small subset of the dataset for testing.
    """
    logging.info("Loading Common Corpus dataset metadata...")

    # Load a small subset of the dataset
    dataset = load_dataset("PleIAs/common_corpus", split=f"train[:{sample_size}]")

    logging.info(f"Loaded {len(dataset)} samples from the dataset.")
    return dataset

def preprocess_dataset_with_pca(dataset, model_name="distilbert-base-uncased", device="cpu", target_power=3):
    """
    Preprocess dataset:
    1) Extract embeddings using a Transformer model.
    2) Reduce dimensions using PCA for quantum encoding compatibility.
    """
    logging.info(f"Preprocessing dataset with model: {model_name} and PCA...")
    embedder = TransformerEmbedder(model_name=model_name, device=device)
    reducer = PCA(n_components=2 ** target_power)

    def process_text(text):
        embeddings = embedder.get_token_embeddings(text)  # Extract embeddings
        return reducer.fit_transform(embeddings)          # Apply PCA

    dataset = dataset.map(lambda batch: {"embeddings": [process_text(t) for t in batch["text"]]}, batched=True)
    return dataset

def plot_embeddings_pca(embeddings, title="PCA Embeddings"):
    """
    Visualize embeddings reduced to 2D space with PCA.
    """
    plt.figure(figsize=(8, 6))
    plt.scatter(embeddings[:, 0], embeddings[:, 1], alpha=0.7, edgecolor='k')
    plt.title(title)
    plt.xlabel("PCA Component 1")
    plt.ylabel("PCA Component 2")
    plt.grid(True)
    plt.show()

def plot_quantum_distribution(quantum_result, sample_id):
    """
    Plot the quantum probability distribution for a specific sample.
    """
    plt.figure(figsize=(10, 5))
    plt.bar(range(len(quantum_result)), quantum_result, alpha=0.7)
    plt.title(f"Quantum Probability Distribution for Sample {sample_id}")
    plt.xlabel("Quantum State Index")
    plt.ylabel("Probability")
    plt.grid(True)
    plt.show()

def classical_baseline(embeddings):
    """
    Example classical baseline function.
    Computes the average of embeddings as a simple baseline.
    """
    return np.mean(embeddings, axis=(0, 1)) if len(embeddings) else None

def compare_classical_quantum(classical_result, quantum_results):
    """
    Compare classical embeddings with quantum probability distributions.
    """
    avg_quantum = np.mean(quantum_results, axis=0)

    plt.figure(figsize=(10, 6))
    plt.plot(classical_result, label="Classical Representation", linestyle="--", marker="o")
    plt.plot(avg_quantum, label="Quantum Average Representation", linestyle="-", marker="x")
    plt.title("Classical vs Quantum Representation")
    plt.xlabel("Feature Dimension / Quantum State Index")
    plt.ylabel("Value / Probability")
    plt.legend()
    plt.grid(True)
    plt.show()

def main_pipeline_demo_with_visualizations(sample_size=10, use_ibm=False, target_power=3):
    """
    Refined pipeline with preprocessing, quantum encoding, and visualizations.
    """
    # Step 1: Load dataset
    dataset = load_common_corpus_metadata(sample_size=sample_size)

    # Step 2: Preprocess dataset with PCA
    logging.info("Preprocessing dataset with Transformers and PCA...")
    dataset = preprocess_dataset_with_pca(dataset, model_name="distilbert-base-uncased", device="cpu", target_power=target_power)

    # Step 3: Extract embeddings
    embeddings = np.vstack([sample["embeddings"] for sample in dataset])

    # Step 4: Visualize PCA-reduced embeddings
    plot_embeddings_pca(embeddings, title="PCA of Embeddings")

    # Step 5: Quantum backend and encoding
    backend = get_ibm_backend(min_qubits=5) if use_ibm else FakeAthens()
    quantum_results = process_batch_with_quantum_encoder(
        batch_embeddings=[sample["embeddings"] for sample in dataset],
        n_qubits=target_power,  # Number of qubits
        group_size=4,
        multi_level=True,
        backend=backend
    )

    # Step 6: Compute classical baseline
    classical_result = classical_baseline(embeddings)

    # Step 7: Visualize quantum results and compare
    for i, qr in enumerate(quantum_results[:3]):  # Show the first 3 samples
        if qr is not None:
            plot_quantum_distribution(qr, sample_id=i)
    compare_classical_quantum(classical_result, quantum_results)

    return quantum_results, classical_result

if __name__ == "__main__":
    logging.basicConfig(level=logging.INFO)
    quantum_dists, cls_baseline = main_pipeline_demo_with_visualizations(
        sample_size=100,
        use_ibm=False,  # Set to True if using IBM Quantum backend
        target_power=3  # Use 3 qubits (dimensionality = 2^3 = 8)
    )


Resolving data files:   0%|          | 0/10009 [00:00<?, ?it/s]

subset_33_2.parquet:   0%|          | 0.00/330M [00:00<?, ?B/s]

subset_33_3.parquet:   0%|          | 0.00/332M [00:00<?, ?B/s]

subset_33_4.parquet:   0%|          | 0.00/336M [00:00<?, ?B/s]

subset_33_5.parquet:   0%|          | 0.00/332M [00:00<?, ?B/s]

...

/usr/local/lib/python3.11/dist-packages/huggingface_hub/file_download.py:651: UserWarning: Not enough free disk space to download the file. The expected file size is: 329.91 MB. The target location /root/.cache/huggingface/hub/datasets--PleIAs--common_corpus/blobs only has 283.69 MB free disk space.
  warnings.warn(


subset_6_3.parquet:   0%|          | 0.00/330M [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/huggingface_hub/file_download.py:651: UserWarning: Not enough free disk space to download the file. The expected file size is: 332.34 MB. The target location /root/.cache/huggingface/hub/datasets--PleIAs--common_corpus/blobs only has 0.00 MB free disk space.
  warnings.warn(


subset_6_4.parquet:   0%|          | 0.00/332M [00:00<?, ?B/s]

OSError: [Errno 28] No space left on device